In [ ]:
import pandas as pd
import json
import re
import math
import psycopg2
import torch
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import time
from itertools import chain
from random import shuffle
import torch.nn.functional as F
from torch.autograd import Variable
from torch.utils.data import DataLoader
from gensim.models import Word2Vec
from gensim.models import KeyedVectors
torch.set_printoptions(precision=10, threshold=None, edgeitems=None, linewidth=None, profile=None)

In [ ]:
def prepare_dataset(prefix_path):
    data={}
    data["aka_name"] = pd.read_csv(prefix_path+'/imdb_data_csv/aka_name.csv',header=None)
    data["aka_title"] = pd.read_csv(prefix_path+'/imdb_data_csv/aka_title.csv',header=None)
    data["cast_info"] = pd.read_csv(prefix_path+'/imdb_data_csv/cast_info.csv',header=None)
    data["char_name"] = pd.read_csv(prefix_path+'/imdb_data_csv/char_name.csv',header=None)
    data["company_name"] = pd.read_csv(prefix_path+'/imdb_data_csv/company_name.csv',header=None)
    data["company_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/company_type.csv',header=None)
    data["comp_cast_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/comp_cast_type.csv',header=None)
    data["complete_cast"] = pd.read_csv(prefix_path+'/imdb_data_csv/complete_cast.csv',header=None)
    data["info_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/info_type.csv',header=None)
    data["keyword"] = pd.read_csv(prefix_path+'/imdb_data_csv/keyword.csv',header=None)
    data["kind_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/kind_type.csv',header=None)
    data["link_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/link_type.csv',header=None)
    data["movie_companies"] = pd.read_csv(prefix_path+'/imdb_data_csv/movie_companies.csv',header=None)
    data["movie_info"] = pd.read_csv(prefix_path+'/imdb_data_csv/movie_info.csv',header=None)
    data["movie_info_idx"] = pd.read_csv(prefix_path+'/imdb_data_csv/movie_info_idx.csv',header=None)
    data["movie_keyword"] = pd.read_csv(prefix_path+'/imdb_data_csv/movie_keyword.csv',header=None)
    data["movie_link"] = pd.read_csv(prefix_path+'/imdb_data_csv/movie_link.csv',header=None)
    data["name"] = pd.read_csv(prefix_path+'/imdb_data_csv/name.csv',header=None)
    data["person_info"] = pd.read_csv(prefix_path+'/imdb_data_csv/person_info.csv',header=None)
    data["role_type"] = pd.read_csv(prefix_path+'/imdb_data_csv/role_type.csv',header=None)
    data["title"] = pd.read_csv(prefix_path+'/imdb_data_csv/title.csv',header=None)
    aka_name_column = [
        'id',
        'person_id',
        'name',
        'imdb_index',
        'name_pcode_cf',
        'name_pcode_nf',
        'surname_pcode',
        'md5sum'
    ]
    aka_title_column = [
        'id',
        'movie_id',
        'title',
        'imdb_index',
        'kind_id',
        'production_year',
        'phonetic_code',
        'episode_of_id',
        'season_nr',
        'episode_nr',
        'note',
        'md5sum'
    ]
    cast_info_column = [
        'id',
        'person_id',
        'movie_id',
        'person_role_id',
        'note',
        'nr_order',
        'role_id'
    ]
    char_name_column = [
        'id',
        'name',
        'imdb_index',
        'imdb_id',
        'name_pcode_nf',
        'surname_pcode',
        'md5sum'
    ]
    comp_cast_type_column = [
        'id',
        'kind'
    ]
    company_name_column = [
        'id',
        'name',
        'country_code',
        'imdb_id',
        'name_pcode_nf',
        'name_pcode_sf',
        'md5sum'
    ]
    company_type_column = [
        'id',
        'kind'
    ]
    complete_cast_column = [
        'id',
        'movie_id',
        'subject_id',
        'status_id'
    ]
    info_type_column = [
        'id',
        'info'
    ]
    keyword_column = [
        'id',
        'keyword',
        'phonetic_code'
    ]
    kind_type_column = [
        'id',
        'kind'
    ]
    link_type_column = [
        'id',
        'link'
    ]
    movie_companies_column = [
        'id',
        'movie_id',
        'company_id',
        'company_type_id',
        'note'
    ]
    movie_info_idx_column = [
        'id',
        'movie_id',
        'info_type_id',
        'info',
        'note'
    ]
    movie_keyword_column = [
        'id',
        'movie_id',
        'keyword_id'
    ]
    movie_link_column = [
        'id',
        'movie_id',
        'linked_movie_id',
        'link_type_id'
    ]
    name_column = [
        'id',
        'name',
        'imdb_index',
        'imdb_id',
        'gender',
        'name_pcode_cf',
        'name_pcode_nf',
        'surname_pcode',
        'md5sum'
    ]
    role_type_column = [
        'id',
        'role'
    ]
    title_column = [
        'id',
        'title',
        'imdb_index',
        'kind_id',
        'production_year',
        'imdb_id',
        'phonetic_code',
        'episode_of_id',
        'season_nr',
        'episode_nr',
        'series_years',
        'md5sum'
    ]
    movie_info_column = [
        'id',
        'movie_id',
        'info_type_id',
        'info',
        'note'
    ]
    person_info_column = [
        'id',
        'person_id',
        'info_type_id',
        'info',
        'note'
    ]
    data["aka_name"].columns = aka_name_column
    data["aka_title"].columns = aka_title_column
    data["cast_info"].columns = cast_info_column
    data["char_name"].columns = char_name_column
    data["company_name"].columns = company_name_column
    data["company_type"].columns = company_type_column
    data["comp_cast_type"].columns = comp_cast_type_column
    data["complete_cast"].columns = complete_cast_column
    data["info_type"].columns = info_type_column
    data["keyword"].columns = keyword_column
    data["kind_type"].columns = kind_type_column
    data["link_type"].columns = link_type_column
    data["movie_companies"].columns = movie_companies_column
    data["movie_info"].columns = movie_info_column
    data["movie_info_idx"].columns = movie_info_idx_column
    data["movie_keyword"].columns = movie_keyword_column
    data["movie_link"].columns = movie_link_column
    data["name"].columns = name_column
    data["person_info"].columns = person_info_column
    data["role_type"].columns = role_type_column
    data["title"].columns = title_column
    
    column2pos = {}
    column2pos['aka_name'] = aka_name_column
    column2pos['aka_title'] = aka_title_column
    column2pos['cast_info'] = cast_info_column
    column2pos['char_name'] = char_name_column
    column2pos['company_name'] = company_name_column
    column2pos['company_type'] = company_type_column
    column2pos['comp_cast_type'] = comp_cast_type_column
    column2pos['complete_cast'] = complete_cast_column
    column2pos['info_type'] = info_type_column
    column2pos['keyword'] = keyword_column
    column2pos['kind_type'] = kind_type_column
    column2pos['link_type'] = link_type_column
    column2pos['movie_companies'] = movie_companies_column
    column2pos['movie_info'] = movie_info_column
    column2pos['movie_info_idx'] = movie_info_idx_column
    column2pos['movie_keyword'] = movie_keyword_column
    column2pos['movie_link'] = movie_link_column
    column2pos['name'] = name_column
    column2pos['person_info'] = person_info_column
    column2pos['role_type'] = role_type_column
    column2pos['title'] = title_column
    tables = ['aka_name', 'aka_title', 'cast_info', 'char_name', 'company_name', 'company_type', 'comp_cast_type', 'complete_cast', 'info_type', 'keyword', 'kind_type', 'link_type', 'movie_companies', 'movie_info', 'movie_info_idx',
              'movie_keyword', 'movie_link', 'name', 'person_info', 'role_type', 'title']
    indexes = ['aka_name_pkey', 'aka_title_pkey', 'cast_info_pkey', 'char_name_pkey',
               'comp_cast_type_pkey', 'company_name_pkey', 'company_type_pkey', 'complete_cast_pkey',
               'info_type_pkey', 'keyword_pkey', 'kind_type_pkey', 'link_type_pkey', 'movie_companies_pkey',
               'movie_info_idx_pkey', 'movie_keyword_pkey', 'movie_link_pkey', 'name_pkey', 'role_type_pkey',
               'title_pkey', 'movie_info_pkey', 'person_info_pkey', 'company_id_movie_companies',
               'company_type_id_movie_companies', 'info_type_id_movie_info_idx', 'info_type_id_movie_info',
               'info_type_id_person_info', 'keyword_id_movie_keyword', 'kind_id_aka_title', 'kind_id_title',
               'linked_movie_id_movie_link', 'link_type_id_movie_link', 'movie_id_aka_title', 'movie_id_cast_info',
               'movie_id_complete_cast', 'movie_id_movie_ companies', 'movie_id_movie_info_idx',
               'movie_id_movie_keyword', 'movie_id_movie_link', 'movie_id_movie_info', 'person_id_aka_name',
               'person_id_cast_info', 'person_id_person_info', 'person_role_id_cast_info', 'role_id_cast_info']
    indexes_id = {}
    for idx, index in enumerate(indexes):
        indexes_id[index] = idx + 1
    physic_ops_id = {'Materialize':1, 'Sort':2, 'Hash':3, 'Merge Join':4, 'Bitmap Index Scan':5,
     'Index Only Scan':6, 'BitmapAnd':7, 'Nested Loop':8, 'Aggregate':9, 'Result':10,
     'Hash Join':11, 'Seq Scan':12, 'Bitmap Heap Scan':13, 'Index Scan':14, 'BitmapOr':15}
    strategy_id = {'Plain':1}
    compare_ops_id = {'=':1, '>':2, '<':3, '!=':4, '~~':5, '!~~':6, '!Null': 7, '>=':8, '<=':9}
    bool_ops_id = {'AND':1,'OR':2}
    tables_id = {}
    columns_id = {}
    table_id = 1
    column_id = 1
    for table_name in tables:
        tables_id[table_name] = table_id
        table_id += 1
        for column in column2pos[table_name]:
            columns_id[table_name+'.'+column] = column_id
            column_id += 1 
    return data, indexes_id, tables_id, columns_id, physic_ops_id, compare_ops_id, bool_ops_id

In [ ]:
def load_dictionary(path): 
    word_vectors = KeyedVectors.load(path, mmap='r')
    return word_vectors

In [ ]:
def load_numeric_min_max(path):
    with open(path,'r') as f:
        min_max_column = json.loads(f.read())
    return min_max_column

In [129]:
def determine_prefix(column):
    relation_name = column.split('.')[0]
    column_name = column.split('.')[1]
    if relation_name == 'aka_title':
        if column_name == 'title':
            return 'title_'
        else:
            print (column)
            raise
    elif relation_name == 'char_name':
        if column_name == 'name':
            return 'name_'
        elif column_name == 'name_pcode_nf':
            return 'nf_'
        elif column_name == 'surname_pcode':
            return 'surname_'
        else:
            print (column)
            raise
    elif relation_name == 'movie_info_idx':
        if column_name == 'info':
            return 'info_'
        else:
            print (column)
            raise
    elif relation_name == 'title':
        if column_name == 'title':
            return 'title_'
        else:
            print (column)
            raise
    elif relation_name == 'role_type':
        if column_name == 'role':
            return 'role_'
        else:
            print (column)
            raise
    elif relation_name == 'movie_companies':
        if column_name == 'note':
            return 'note_'
        else:
            print (column)
            raise
    elif relation_name == 'info_type':
        if column_name == 'info':
            return 'info_'
        else:
            print (column)
            raise
    elif relation_name == 'company_type':
        if column_name == 'kind':
            return ''
        else:
            print (column)
            raise
    elif relation_name == 'company_name':
        if column_name == 'name':
            return 'cn_name_'
        elif column_name == 'country_code':
            return 'country_'
        else:
            print (column)
            raise
    elif relation_name == 'keyword':
        if column_name == 'keyword':
            return 'keyword_'
        else:
            print (column)
            raise
            
    elif relation_name == 'movie_info':
        if column_name == 'info':
            return ''
        elif column_name == 'note':
            return 'note_'
        else:
            print (column)
            raise
    elif relation_name == 'name':
        if column_name == 'gender':
            return 'gender_'
        elif column_name == 'name':
            return 'name_'
        elif column_name == 'name_pcode_cf':
            return 'cf_'
        elif column_name == 'name_pcode_nf':
            return 'nf_'
        elif column_name == 'surname_pcode':
            return 'surname_'
        else:
            print (column)
            raise
    elif relation_name == 'aka_name':
        if column_name == 'name':
            return 'name_'
        elif column_name == 'name_pcode_cf':
            return 'cf_'
        elif column_name == 'name_pcode_nf':
            return 'nf_'
        elif column_name == 'surname_pcode':
            return 'surname_'
        else:
            print (column)
            raise
    elif relation_name == 'link_type':
        if column_name == 'link':
            return 'link_'
        else:
            print (column)
            raise
    elif relation_name == 'person_info':
        if column_name == 'note':
            return 'note_'
        else:
            print (column)
            raise
    elif relation_name == 'cast_info':
        if column_name == 'note':
            return 'note_'
        else:
            print (column)
            raise
    elif relation_name == 'comp_cast_type':
        if column_name == 'kind':
            return 'kind_'
        else:
            print (column)
            raise
    elif relation_name == 'kind_type':
        if column_name == 'kind':
            return 'kind_'
        else:
            print (column)
            raise
    else:
        print (column)
        raise

def get_representation(value):
    if value in word_vectors:
        embedded_result = np.array(list(word_vectors[value]))
    else:
        embedded_result = np.array([0.0 for _ in range(500)])
    hash_result = np.array([0.0 for _ in range(500)])
    for t in value:
        hash_result[hash(t) % 500] = 1.0
    return np.concatenate((embedded_result, hash_result), 0)

def get_str_representation(value, column):
    vec = np.array([])
    count = 0
    prefix = determine_prefix(column)
    for v in value.split('%'):
        if len(v) > 0:
            if len(vec) == 0:
                vec = get_representation(prefix+v)
                count = 1
            else:
                new_vec = get_representation(prefix+v)
                vec = vec + new_vec
                count += 1
    if count > 0:
        vec = vec / float(count)
    return vec

def encode_condition_op(condition_op, relation_name, index_name):
    # bool_operator + left_value + compare_operator + right_value
    if condition_op == None:
        vec = [0 for _ in range(condition_op_dim)]
    elif condition_op['op_type'] == 'Bool':
        idx = bool_ops_id[condition_op['operator']]
        vec = [0 for _ in range(bool_ops_total_num)]
        vec[idx-1] = 1
    else:
        operator = condition_op['operator']
        left_value = condition_op['left_value']
        if re.match(r'.+\..+', left_value) == None:
            if relation_name == None:
                relation_name = index_name.split(left_value)[1].strip('_')
            left_value = relation_name + '.' + left_value
        else:
            relation_name = left_value.split('.')[0]
        left_value_idx = columns_id[left_value]
        left_value_vec = [0 for _ in range(column_total_num)]
        left_value_vec[left_value_idx-1] = 1
        right_value = condition_op['right_value']
        column_name = left_value.split('.')[1]
        if re.match(r'^[a-z][a-zA-Z0-9_]*\.[a-z][a-zA-Z0-9_]*$', right_value) != None and right_value.split('.')[0] in data:
            operator_idx = compare_ops_id[operator]
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value_idx = columns_id[right_value]
            right_value_vec = [0]
            left_value_vec[right_value_idx-1] = 1
        elif data[relation_name].dtypes[column_name] == 'int64' or data[relation_name].dtypes[column_name] == 'float64':
            right_value = float(right_value)
            value_max = min_max_column[relation_name][column_name]['max']
            value_min = min_max_column[relation_name][column_name]['min']
            right_value_vec = [(right_value - value_min) / (value_max - value_min)]
            operator_idx = compare_ops_id[operator]
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1            
        elif re.match(r'^__LIKE__', right_value) != None:
            operator_idx = compare_ops_id['~~']
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value = right_value.strip('\'')[8:]
            right_value_vec = get_str_representation(right_value, left_value).tolist()
        elif re.match(r'^__NOTLIKE__', right_value) != None:
            operator_idx = compare_ops_id['!~~']
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value = right_value.strip('\'')[11:]
            right_value_vec = get_str_representation(right_value, left_value).tolist()
        elif re.match(r'^__NOTEQUAL__', right_value) != None:
            operator_idx = compare_ops_id['!=']
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value = right_value.strip('\'')[12:]
            right_value_vec = get_str_representation(right_value, left_value).tolist()
        elif re.match(r'^__ANY__', right_value) != None:
            operator_idx = compare_ops_id['=']
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value = right_value.strip('\'')[7:].strip('{}')
            right_value_vec = []
            count = 0
            for v in right_value.split(','):
                v = v.strip('"').strip('\'')
                if len(v) > 0:
                    count += 1
                    vec = get_str_representation(v, left_value).tolist()
                    if len(right_value_vec) == 0:
                        right_value_vec = [0 for _ in vec]
                    for idx, vv in enumerate(vec):
                        right_value_vec[idx] += vv
            for idx in range(len(right_value_vec)):
                right_value_vec[idx] /= len(right_value.split(','))
        elif right_value == 'None':
            operator_idx = compare_ops_id['!Null']
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            if operator == 'IS':
                right_value_vec = [1]
            elif operator == '!=':
                right_value_vec = [0]
            else:
                print (operator)
                raise
        else:
#             print (left_value, operator, right_value)
            operator_idx = compare_ops_id[operator]
            operator_vec = [0 for _ in range(compare_ops_total_num)]
            operator_vec[operator_idx-1] = 1
            right_value_vec = get_str_representation(right_value, left_value).tolist()
        vec = [0 for _ in range(bool_ops_total_num)]
        vec = vec + left_value_vec + operator_vec + right_value_vec
    num_pad = condition_op_dim - len(vec)
    result = np.pad(vec, (0, num_pad), 'constant')
#     print 'condition op: ', result
    return result

def encode_sample(sample):
    return np.array([int(i) for i in sample])

def bitand(sample1, sample2):
    return np.minimum(sample1, sample2)

def encode_node_job(node, condition_max_num):
    # operator + first_condition + second_condition + relation
    extra_info_num = max(column_total_num, table_total_num, index_total_num)
    operator_vec = np.array([0 for _ in range(physic_op_total_num)])
    
    extra_info_vec = np.array([0 for _ in range(extra_info_num)])
    condition1_vec = np.array([[0 for _ in range(condition_op_dim)] for _ in range(condition_max_num)])
    condition2_vec = np.array([[0 for _ in range(condition_op_dim)] for _ in range(condition_max_num)])
    ### Samples Starts
    sample_vec = np.array([1 for _ in range(1000)])
    ### Samples Ends
    has_condition = 0
    if node != None:
        operator = node['node_type']
        operator_idx = physic_ops_id[operator]
        operator_vec[operator_idx-1] = 1
        if operator == 'Materialize' or operator == 'BitmapAnd' or operator == 'Result':
            pass
        elif operator == 'Sort':
            for key in node['sort_keys']:
                extra_info_inx = columns_id[key]
                extra_info_vec[extra_info_inx-1] = 1
        elif operator == 'Hash Join' or operator == 'Merge Join' or operator == 'Nested Loop':
            condition1_vec = encode_condition(node['condition'], None, None, condition_max_num)
        elif operator == 'Aggregate':
            for key in node['group_keys']:
                extra_info_inx = columns_id[key]
                extra_info_vec[extra_info_inx-1] = 1
        elif operator == 'Seq Scan' or operator == 'Bitmap Heap Scan' or operator == 'Index Scan' or operator == 'Bitmap Index Scan' or operator == 'Index Only Scan':
            relation_name = node['relation_name']
            index_name = node['index_name']
            if relation_name != None:
                extra_info_inx = tables_id[relation_name]
            else:
                extra_info_inx = indexes_id[index_name]
            extra_info_vec[extra_info_inx-1] = 1
            condition1_vec = encode_condition(node['condition_filter'], relation_name, index_name, condition_max_num)
            condition2_vec = encode_condition(node['condition_index'], relation_name, index_name, condition_max_num)
            if 'bitmap' in node:
                ### Samples Starts
                sample_vec = encode_sample(node['bitmap'])
                ### Samples Ends
                has_condition = 1
            if 'bitmap_filter' in node:
                ### Samples Starts
                sample_vec = bitand(encode_sample(node['bitmap_filter']), sample_vec)
                ### Samples Ends
                has_condition = 1
            if 'bitmap_index' in node:
                ### Samples Starts
                sample_vec = bitand(encode_sample(node['bitmap_index']), sample_vec)
                ### Samples Ends
                has_condition = 1
            
#     print 'operator: ', operator_vec
#     print 'extra_infos: ', extra_info_vec
    return operator_vec, extra_info_vec, condition1_vec, condition2_vec, sample_vec, has_condition

def encode_condition(condition, relation_name, index_name, condition_max_num):
    if len(condition) == 0:
        vecs = [[0 for _ in range(condition_op_dim)]]
    else:
        vecs = [encode_condition_op(condition_op, relation_name, index_name) for condition_op in condition]
    num_pad = condition_max_num - len(vecs)
    result = np.pad(vecs, ((0, num_pad),(0,0)), 'constant')
    return result

class TreeNode(object):
    def __init__(self, current_vec, parent, idx, level_id):
        self.item = current_vec
        self.idx = idx
        self.level_id = level_id
        self.parent = parent
        self.children = []
    def get_parent(self):
        return self.parent
    def get_item(self):
        return self.item
    def get_children(self):
        return self.children
    def add_child(self, child):
        self.children.append(child)
    def get_idx(self):
        return self.idx
    def __str__(self):
        return 'level_id: ' + self.level_id + '; idx: ' + self.idx

def recover_tree(vecs, parent, start_idx):
    if len(vecs) == 0:
        return vecs, start_idx
    if vecs[0] == None:
        return vecs[1:], start_idx+1
    node = TreeNode(vecs[0], parent, start_idx, -1)
    while True:
        vecs, start_idx = recover_tree(vecs[1:], node, start_idx+1)
        parent.add_child(node)
        if len(vecs) == 0:
            return vecs, start_idx
        if vecs[0] == None:
            return vecs[1:], start_idx+1
        node = TreeNode(vecs[0], parent, start_idx, -1)

def dfs_tree_to_level(root, level_id, nodes_by_level):
    root.level_id = level_id
    if len(nodes_by_level) <= level_id:
        nodes_by_level.append([])
    nodes_by_level[level_id].append(root)
    root.idx = len(nodes_by_level[level_id])
    for c in root.get_children():
        dfs_tree_to_level(c, level_id+1, nodes_by_level)

def debug_nodes_by_level(nodes_by_level):
    for nodes in nodes_by_level:
        for node in nodes:
            whitespace = ''
            for i in range(node.level_id):
                whitespace += ' '
            print (whitespace + 'level_id: ' + str(node.level_id))
            print (whitespace + 'idx: ' + str(node.idx))
        
def encode_plan_job(plan, condition_max_num):
    operators, extra_infos, condition1s, condition2s, samples, condition_masks = [], [], [], [], [], []
    mapping = []
    
    nodes_by_level = []
    node = TreeNode(plan[0], None, 0, -1)
    recover_tree(plan[1:], node, 1)
    dfs_tree_to_level(node, 0, nodes_by_level)
    
#     print (plan)
#     debug_nodes_by_level(nodes_by_level)
    
    
    for level in nodes_by_level:
        operators.append([])
        extra_infos.append([])
        condition1s.append([])
        condition2s.append([])
        samples.append([])
        condition_masks.append([])
        mapping.append([])
        for node in level:
            operator, extra_info, condition1, condition2, sample, condition_mask = encode_node_job(node.item, condition_max_num)
            operators[-1].append(operator)
            extra_infos[-1].append(extra_info)
            condition1s[-1].append(condition1)
            condition2s[-1].append(condition2)
            samples[-1].append(sample)
            condition_masks[-1].append(condition_mask)
            if len(node.children) == 2:
                mapping[-1].append([n.idx for n in node.children])
            elif len(node.children) == 1:
                mapping[-1].append([node.children[0].idx, 0])
            else:
                mapping[-1].append([0, 0])
#     num_pad = plan_node_max_num - len(operators)
#     masks = [0 for _ in range(plan_node_max_num)]
#     for i in range(len(operators)):
#         if operators[i].sum() > 0:
#             masks[i] = 1
#         else:
#             masks[i] = 0
#     masks = np.array(masks)
#     condition_masks = np.array(condition_masks)
#     operators, extra_infos, condition1s, condition2s = np.pad(operators, ((0, num_pad), (0,0)), 'constant'), np.pad(extra_infos, ((0, num_pad), (0,0)), 'constant'),np.pad(condition1s, ((0, num_pad), (0,0), (0,0)), 'constant'),np.pad(condition2s, ((0, num_pad), (0,0), (0,0)), 'constant')
#     samples = np.pad(samples, ((0, num_pad), (0,0)), 'constant')
#     condition_masks = np.pad(condition_masks, (0, num_pad), 'constant')
    return operators, extra_infos, condition1s, condition2s, samples, condition_masks, mapping




In [130]:
def normalize_label(labels, mini, maxi):
    labels_norm = (torch.log(labels) - mini) / (maxi - mini)
    labels_norm = torch.min(labels_norm, torch.ones_like(labels_norm))
    labels_norm = torch.max(labels_norm, torch.zeros_like(labels_norm))
    return labels_norm

def unnormalize(vecs, mini, maxi):
    return torch.exp(vecs * (maxi - mini) + mini)

In [131]:
def obtain_upper_bound_query_size(path):
    plan_node_max_num = 0
    condition_max_num = 0
    cost_label_max = 0.0
    cost_label_min = 9999999999.0
    card_label_max = 0.0
    card_label_min = 9999999999.0
    plans = []
    with open(path, 'r') as f:
        for plan in f.readlines():
            plan = json.loads(plan)
            plans.append(plan)
            cost = plan['cost']
            cardinality = plan['cardinality']
            if cost > cost_label_max:
                cost_label_max = cost
            elif cost < cost_label_min:
                cost_label_min = cost
            if cardinality > card_label_max:
                card_label_max = cardinality
            elif cardinality < card_label_min:
                card_label_min = cardinality
            sequence = plan['seq']
            plan_node_num = len(sequence)
            if plan_node_num > plan_node_max_num:
                plan_node_max_num = plan_node_num
            for node in sequence:
                if node == None:
                    continue
                if 'condition_filter' in node:
                    condition_num = len(node['condition_filter'])
                    if condition_num > condition_max_num:
                        condition_max_num = condition_num
                if 'condition_index' in node:
                    condition_num = len(node['condition_index'])
                    if condition_num > condition_max_num:
                        condition_max_num = condition_num
    cost_label_min, cost_label_max = math.log(cost_label_min), math.log(cost_label_max)
    card_label_min, card_label_max = math.log(card_label_min), math.log(card_label_max)
    print (plan_node_max_num, condition_max_num)
    print (cost_label_min, cost_label_max)
    print (card_label_min, card_label_max)
    return plan_node_max_num, condition_max_num, cost_label_min, cost_label_max, card_label_min, card_label_max

In [132]:
def merge_plans_level(level1, level2, isMapping=False):
    for idx, level in enumerate(level2):
        if idx >= len(level1):
            level1.append([])
        if isMapping:
            if idx < len(level1) - 1:
                base = len(level1[idx+1])
                for i in range(len(level)):
                    if level[i][0] > 0:
                        level[i][0] += base
                    if level[i][1] > 0:
                        level[i][1] += base
        level1[idx] += level
    return level1

def make_data_job(plans):
    target_cost_batch = []
    target_card_batch = []
    operators_batch = []
    extra_infos_batch = []
    condition1s_batch = []
    condition2s_batch = []
    node_masks_batch = []
    samples_batch = []
    condition_masks_batch = []
    mapping_batch = []
    
    for plan in plans:
        target_cost = plan['cost']
        target_cardinality = plan['cardinality']
        target_cost_batch.append(target_cost)
        target_card_batch.append(target_cardinality)
        plan = plan['seq']
        operators, extra_infos, condition1s, condition2s, samples, condition_masks, mapping = encode_plan_job(plan, condition_max_num)
        
        operators_batch = merge_plans_level(operators_batch, operators)
        extra_infos_batch = merge_plans_level(extra_infos_batch, extra_infos)
        condition1s_batch = merge_plans_level(condition1s_batch, condition1s)
        condition2s_batch = merge_plans_level(condition2s_batch, condition2s)
        samples_batch = merge_plans_level(samples_batch, samples)
        condition_masks_batch = merge_plans_level(condition_masks_batch, condition_masks)
        mapping_batch = merge_plans_level(mapping_batch, mapping, True)
    max_nodes = 0
    for o in operators_batch:
        if len(o) > max_nodes:
            max_nodes = len(o)
    print (max_nodes)
    print (len(condition2s_batch))
    operators_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0)), 'constant') for v in operators_batch])
    extra_infos_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0)), 'constant') for v in extra_infos_batch])
    condition1s_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0),(0,0)), 'constant') for v in condition1s_batch])
    condition2s_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0),(0,0)), 'constant') for v in condition2s_batch])
    samples_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0)), 'constant') for v in samples_batch])
    condition_masks_batch = np.array([np.pad(v, (0, max_nodes - len(v)), 'constant') for v in condition_masks_batch])
    mapping_batch = np.array([np.pad(v, ((0, max_nodes - len(v)),(0,0)), 'constant') for v in mapping_batch])
    
    print ('operators_batch: ', operators_batch.shape)
    
    target_cost_batch = torch.FloatTensor(target_cost_batch)
    target_card_batch = torch.FloatTensor(target_card_batch)
    operators_batch = torch.FloatTensor([operators_batch])
    extra_infos_batch = torch.FloatTensor([extra_infos_batch])
    condition1s_batch = torch.FloatTensor([condition1s_batch])
    condition2s_batch = torch.FloatTensor([condition2s_batch])
    samples_batch = torch.FloatTensor([samples_batch])
    condition_masks_batch = torch.FloatTensor([condition_masks_batch])
    mapping_batch = torch.FloatTensor([mapping_batch])
    
    target_cost_batch = normalize_label(target_cost_batch, cost_label_min, cost_label_max)
    target_card_batch = normalize_label(target_card_batch, card_label_min, card_label_max)
    
    return (target_cost_batch, target_card_batch, operators_batch, extra_infos_batch, condition1s_batch, condition2s_batch, samples_batch, condition_masks_batch, mapping_batch)

def chunks(arr, batch_size):
    return [arr[i:i+batch_size] for i in range(0, len(arr), batch_size)]

def save_data_job(plans, istest = False, batch_size=64, directory='/home/sunji/learnedcardinality/job'):
    if istest:
        suffix = 'test_'
    else:
        suffix = ''
    batch_id = 0
    for batch_id, plans_batch in enumerate(chunks(plans, batch_size)):
        print ('batch_id', batch_id, len(plans_batch))
        target_cost_batch, target_cardinality_batch, operators_batch, extra_infos_batch, condition1s_batch, condition2s_batch, samples_batch, condition_masks_batch, mapping_batch = make_data_job(plans_batch)
        np.save(directory+'/target_cost_'+suffix+str(batch_id)+'.np', target_cost_batch.numpy())
        np.save(directory+'/target_cardinality_'+suffix+str(batch_id)+'.np', target_cardinality_batch.numpy())
        np.save(directory+'/operators_'+suffix+str(batch_id)+'.np', operators_batch.numpy())
        np.save(directory+'/extra_infos_'+suffix+str(batch_id)+'.np', extra_infos_batch.numpy())
        np.save(directory+'/condition1s_'+suffix+str(batch_id)+'.np', condition1s_batch.numpy())
        np.save(directory+'/condition2s_'+suffix+str(batch_id)+'.np', condition2s_batch.numpy())
        np.save(directory+'/samples_'+suffix+str(batch_id)+'.np', samples_batch.numpy())
        np.save(directory+'/condition_masks_'+suffix+str(batch_id)+'.np', condition_masks_batch.numpy())
        np.save(directory+'/mapping_'+suffix+str(batch_id)+'.np', mapping_batch.numpy())
        print ('saved: ', str(batch_id))

def get_batch_job(batch_id, istest=False, directory='/home/sunji/learnedcardinality/job'):
    if istest:
        suffix = 'test_'
    else:
        suffix = ''
    target_cost_batch = np.load(directory+'/target_cost_'+suffix+str(batch_id)+'.np.npy')
    target_cardinality_batch = np.load(directory+'/target_cardinality_'+suffix+str(batch_id)+'.np.npy')
    operators_batch = np.load(directory+'/operators_'+suffix+str(batch_id)+'.np.npy')
    extra_infos_batch = np.load(directory+'/extra_infos_'+suffix+str(batch_id)+'.np.npy')
    condition1s_batch = np.load(directory+'/condition1s_'+suffix+str(batch_id)+'.np.npy')
    condition2s_batch = np.load(directory+'/condition2s_'+suffix+str(batch_id)+'.np.npy')
    samples_batch = np.load(directory+'/samples_'+suffix+str(batch_id)+'.np.npy')
    condition_masks_batch = np.load(directory+'/condition_masks_'+suffix+str(batch_id)+'.np.npy')
    mapping_batch = np.load(directory+'/mapping_'+suffix+str(batch_id)+'.np.npy')
    return target_cost_batch, target_cardinality_batch, operators_batch, extra_infos_batch, condition1s_batch, condition2s_batch, samples_batch, condition_masks_batch, mapping_batch

In [133]:
def encode_train_plan_seq_save(path, batch_size=64, directory='/home/sunji/learnedcardinality/job'):
    test_plans = []
    with open(path, 'r') as f:
        for idx, seq in enumerate(f.readlines()):
            plan = json.loads(seq)
            test_plans.append(plan)
#     shuffle(test_plans)
    save_data_job(plans=test_plans, batch_size=batch_size, directory=directory)

def encode_test_plan_seq_save(path, batch_size=64, directory='/home/sunji/learnedcardinality/job'):
    test_plans = []
    with open(path, 'r') as f:
        for idx, seq in enumerate(f.readlines()):
            plan = json.loads(seq)
            test_plans.append(plan)
#     shuffle(test_plans)
    save_data_job(plans=test_plans, istest=True, batch_size=batch_size, directory=directory)

In [134]:
class Representation(nn.Module):
    def __init__(self, input_dim, hidden_dim, hid_dim, middle_result_dim, task_num):
        super(Representation, self).__init__()
        self.hidden_dim = hidden_dim
        self.lstm1 = nn.LSTM(input_dim, hidden_dim, batch_first=True)
        self.batch_norm1 = nn.BatchNorm1d(hid_dim)
        # The linear layer that maps from hidden state space to tag space
        
        self.sample_mlp = nn.Linear(1000, hid_dim)
        self.condition_mlp = nn.Linear(hidden_dim, hid_dim)
#         self.out_mlp1 = nn.Linear(hidden_dim, middle_result_dim)
#         self.hid_mlp1 = nn.Linear(15+108+2*hid_dim, hid_dim)
#         self.out_mlp1 = nn.Linear(hid_dim, middle_result_dim)
        
        self.lstm2 = nn.LSTM(15+108+2*hid_dim, hidden_dim, batch_first=True)
#         self.lstm2_binary = nn.LSTM(15+108+2*hid_dim, hidden_dim, batch_first=True)
#         self.lstm2_binary = nn.LSTM(15+108+2*hid_dim, hidden_dim, batch_first=True)
        self.batch_norm2 = nn.BatchNorm1d(hidden_dim)
        # The linear layer that maps from hidden state space to tag space
        self.hid_mlp2_task1 = nn.Linear(hidden_dim, hid_dim)
        self.hid_mlp2_task2 = nn.Linear(hidden_dim, hid_dim)
        self.batch_norm3 = nn.BatchNorm1d(hid_dim)
        self.hid_mlp3_task1 = nn.Linear(hid_dim, hid_dim)
        self.hid_mlp3_task2 = nn.Linear(hid_dim, hid_dim)
        self.out_mlp2_task1 = nn.Linear(hid_dim, 1)
        self.out_mlp2_task2 = nn.Linear(hid_dim, 1)
    #         self.hidden2values2 = nn.Linear(hidden_dim, action_num)

    def init_hidden(self, hidden_dim, batch_size=1):
        # Before we've done anything, we dont have any hidden state.
        # Refer to the Pytorch documentation to see exactly
        # why they have this dimensionality.
        # The axes semantics are (num_layers, minibatch_size, hidden_dim)
        return (torch.zeros(1, batch_size, hidden_dim),
                torch.zeros(1, batch_size, hidden_dim))
    
    def forward(self, operators, extra_infos, condition1s, condition2s, samples, condition_masks, mapping):
        # condition1
        batch_size = 0
        for i in range(operators.size()[1]):
            if operators[0][i].sum(0) != 0:
                batch_size += 1
            else:
                break
        print ('batch_size: ', batch_size)
        
#         print (operators.size())
#         print (extra_infos.size())
#         print (condition1s.size())
#         print (condition2s.size())
#         print (samples.size())
#         print (condition_masks.size())
#         print (mapping.size())
        
#         torch.Size([14, 133, 15])
#         torch.Size([14, 133, 108])
#         torch.Size([14, 133, 13, 1119])
#         torch.Size([14, 133, 13, 1119])
#         torch.Size([14, 133, 1000])
#         torch.Size([14, 133, 1])
#         torch.Size([14, 133, 2])
        
        num_level = condition1s.size()[0]
        num_node_per_level = condition1s.size()[1]
        num_condition_per_node = condition1s.size()[2]
        condition_op_length = condition1s.size()[3]
        
        inputs = condition1s.view(num_level * num_node_per_level, num_condition_per_node, condition_op_length)
        hidden = self.init_hidden(self.hidden_dim, num_level * num_node_per_level)
        
        out, hid = self.lstm1(inputs, hidden)
        last_output1 = hid[0].view(num_level * num_node_per_level, -1)
        
        # condition2
        num_level = condition2s.size()[0]
        num_node_per_level = condition2s.size()[1]
        num_condition_per_node = condition2s.size()[2]
        condition_op_length = condition2s.size()[3]
        
        inputs = condition2s.view(num_level * num_node_per_level, num_condition_per_node, condition_op_length)
        hidden = self.init_hidden(self.hidden_dim, num_level * num_node_per_level)
        
        out, hid = self.lstm1(inputs, hidden)
        last_output2 = hid[0].view(num_level * num_node_per_level, -1)
        
        last_output1 = F.relu(self.condition_mlp(last_output1))
        last_output2 = F.relu(self.condition_mlp(last_output2))
        last_output = (last_output1 + last_output2) / 2
        last_output = self.batch_norm1(last_output).view(num_level, num_node_per_level, -1)
        
#         print (last_output.size())
#         torch.Size([14, 133, 256])
        
        sample_output = F.relu(self.sample_mlp(samples))
        sample_output = sample_output * condition_masks

        out = torch.cat((operators, extra_infos, last_output, sample_output), 2)
#         print (out.size())
#         torch.Size([14, 133, 635])
#         out = out * node_masks
        start = time.time()
        hidden = self.init_hidden(self.hidden_dim, num_node_per_level)
        last_level = out[num_level-1].view(num_node_per_level, 1, -1)
#         torch.Size([133, 1, 635])
        _, (hid, cid) = self.lstm2(last_level, hidden)
        mapping = mapping.long()
        for idx in reversed(range(0, num_level-1)):
            mapp_left = mapping[idx][:,0]
            mapp_right = mapping[idx][:,1]
            pad = torch.zeros_like(hid)[:,0].unsqueeze(1)
            next_hid = torch.cat((pad, hid), 1)
            pad = torch.zeros_like(cid)[:,0].unsqueeze(1)
            next_cid = torch.cat((pad, cid), 1)
            hid_left = torch.index_select(next_hid, 1, mapp_left)
            cid_left = torch.index_select(next_cid, 1, mapp_left)
            hid_right = torch.index_select(next_hid, 1, mapp_right)
            cid_right = torch.index_select(next_cid, 1, mapp_right)
            hid = (hid_left + hid_right) / 2
            cid = (cid_left + cid_right) / 2
            last_level = out[idx].view(num_node_per_level, 1, -1)
            _, (hid, cid) = self.lstm2(last_level, (hid, cid))
        output = hid[0]
#         print (output.size())
#         torch.Size([133, 128])
        end = time.time()
        print ('Forest Evaluate Running Time: ', end - start)
        last_output = output[0:batch_size]
        out = self.batch_norm2(last_output)
        
        out_task1 = F.relu(self.hid_mlp2_task1(out))
        out_task1 = self.batch_norm3(out_task1)
        out_task1 = F.relu(self.hid_mlp3_task1(out_task1))
        out_task1 = self.out_mlp2_task1(out_task1)
        out_task1 = F.sigmoid(out_task1)
        
        out_task2 = F.relu(self.hid_mlp2_task2(out))
        out_task2 = self.batch_norm3(out_task2)
        out_task2 = F.relu(self.hid_mlp3_task2(out_task2))
        out_task2 = self.out_mlp2_task2(out_task2)
        out_task2 = F.sigmoid(out_task2)
#         print 'out: ', out.size()
        # batch_size * task_num
        return out_task1, out_task2

In [135]:
def qerror_loss(preds, targets, mini, maxi):
    qerror = []
    preds = unnormalize(preds, mini, maxi)
    targets = unnormalize(targets, mini, maxi)
    for i in range(len(targets)):
        if (preds[i] > targets[i]).cpu().data.numpy()[0]:
            qerror.append(preds[i]/targets[i])
        else:
            qerror.append(targets[i]/preds[i])
    return torch.mean(torch.cat(qerror)), torch.median(torch.cat(qerror)), torch.max(torch.cat(qerror)), torch.argmax(torch.cat(qerror))

def train(train_start, train_end, validate_start, validate_end, num_epochs):
    input_dim = condition_op_dim
    hidden_dim = 128
    hid_dim = 256
    middle_result_dim = 128
    task_num = 2
    model = Representation(input_dim, hidden_dim, hid_dim, middle_result_dim, task_num)
    optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
    model.train()
    start = time.time()
    for epoch in range(num_epochs):
        cost_loss_total = 0.
        card_loss_total = 0.
        model.train()
        for batch_idx in range(train_start, train_end):
            print ('batch_idx: ', batch_idx)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping = get_batch_job(batch_idx)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping = torch.FloatTensor(target_cost), torch.FloatTensor(target_cardinality),torch.FloatTensor(operatorss),torch.FloatTensor(extra_infoss),torch.FloatTensor(condition1ss),torch.FloatTensor(condition2ss), torch.FloatTensor(sampless), torch.FloatTensor(condition_maskss), torch.FloatTensor(mapping)
            operatorss, extra_infoss, condition1ss, condition2ss, condition_maskss = operatorss.squeeze(0), extra_infoss.squeeze(0), condition1ss.squeeze(0), condition2ss.squeeze(0), condition_maskss.squeeze(0).unsqueeze(2)
            sampless = sampless.squeeze(0)
            mapping = mapping.squeeze(0)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss = Variable(target_cost), Variable(target_cardinality), Variable(operatorss), Variable(extra_infoss), Variable(condition1ss), Variable(condition2ss)
            sampless = Variable(sampless)
            optimizer.zero_grad()
            estimate_cost,estimate_cardinality = model(operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping)
            target_cost = target_cost
            target_cardinality = target_cardinality
            cost_loss,cost_loss_median,cost_loss_max,cost_max_idx = qerror_loss(estimate_cost, target_cost, cost_label_min, cost_label_max)
            card_loss,card_loss_median,card_loss_max,card_max_idx = qerror_loss(estimate_cardinality, target_cardinality, card_label_min, card_label_max)
            print (card_loss.item(),card_loss_median.item(),card_loss_max.item(),card_max_idx.item())
            loss = cost_loss + card_loss
            cost_loss_total += cost_loss.item()
            card_loss_total += card_loss.item()
            start = time.time()
            loss.backward()
            optimizer.step()
            end = time.time()
            print ('batchward time: ',end - start)
        batch_num = train_end - train_start
        print("Epoch {}, training cost loss: {}, training card loss: {}".format(epoch, cost_loss_total/batch_num, card_loss_total/batch_num))

        cost_loss_total = 0.
        card_loss_total = 0.
        for batch_idx in range(validate_start, validate_end):
            print ('batch_idx: ', batch_idx)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping = get_batch_job(batch_idx)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping = torch.FloatTensor(target_cost), torch.FloatTensor(target_cardinality),torch.FloatTensor(operatorss),torch.FloatTensor(extra_infoss),torch.FloatTensor(condition1ss),torch.FloatTensor(condition2ss), torch.FloatTensor(sampless), torch.FloatTensor(condition_maskss), torch.FloatTensor(mapping)
            operatorss, extra_infoss, condition1ss, condition2ss, condition_maskss = operatorss.squeeze(0), extra_infoss.squeeze(0), condition1ss.squeeze(0), condition2ss.squeeze(0), condition_maskss.squeeze(0).unsqueeze(2)
            sampless = sampless.squeeze(0)
            mapping = mapping.squeeze(0)
            target_cost, target_cardinality, operatorss, extra_infoss, condition1ss, condition2ss = Variable(target_cost), Variable(target_cardinality), Variable(operatorss), Variable(extra_infoss), Variable(condition1ss), Variable(condition2ss)
            sampless = Variable(sampless)
            estimate_cost,estimate_cardinality = model(operatorss, extra_infoss, condition1ss, condition2ss, sampless, condition_maskss, mapping)
            target_cost = target_cost
            target_cardinality = target_cardinality
            cost_loss,cost_loss_median,cost_loss_max,cost_max_idx = qerror_loss(estimate_cost, target_cost, cost_label_min, cost_label_max)
            card_loss,card_loss_median,card_loss_max,card_max_idx = qerror_loss(estimate_cardinality, target_cardinality, card_label_min, card_label_max)
            print (card_loss.item(),card_loss_median.item(),card_loss_max.item(),card_max_idx.item())
            loss = cost_loss + card_loss
            cost_loss_total += cost_loss.item()
            card_loss_total += card_loss.item()
        batch_num = validate_end - validate_start
        print("Epoch {}, validating cost loss: {}, validating card loss: {}".format(epoch, cost_loss_total/batch_num, card_loss_total/batch_num))
    end = time.time()
    print (end-start)
    return model

In [ ]:
data, indexes_id, tables_id, columns_id, physic_ops_id, compare_ops_id, bool_ops_id = prepare_dataset('/home/sunji/')
print ('data prepared')
word_vectors = load_dictionary('/home/sunji/learnedcardinality/string_words/wordvectors_updated.kv')
print ('word_vectors loaded')
min_max_column = load_numeric_min_max('/home/sunji/learnedcardinality/min_max_vals.json')
print ('min_max loaded')
index_total_num = len(indexes_id)
table_total_num = len(tables_id)
column_total_num = len(columns_id)
physic_op_total_num = len(physic_ops_id)
compare_ops_total_num = len(compare_ops_id)
bool_ops_total_num = len(bool_ops_id)
condition_op_dim = bool_ops_total_num + compare_ops_total_num+column_total_num+1000
condition_op_dim_pro = bool_ops_total_num + column_total_num + 3
plan_node_max_num, condition_max_num, cost_label_min, cost_label_max, card_label_min, card_label_max = obtain_upper_bound_query_size('/home/sunji/learnedcardinality/train_100k_real_plans_seq_sample.json')
print ('query upper size prepared')


In [136]:
encode_train_plan_seq_save('/home/sunji/learnedcardinality/train_100k_real_plans_seq_sample.json')
print ('data encoded')

batch_id 0 64
88
6
operators_batch:  (6, 88, 15)
saved:  0
batch_id 1 64
88
6
operators_batch:  (6, 88, 15)
saved:  1
batch_id 2 64
88
6
operators_batch:  (6, 88, 15)
saved:  2
batch_id 3 64
104
6
operators_batch:  (6, 104, 15)
saved:  3
batch_id 4 64
93
6
operators_batch:  (6, 93, 15)
saved:  4
batch_id 5 64
103
6
operators_batch:  (6, 103, 15)
saved:  5
batch_id 6 64
89
6
operators_batch:  (6, 89, 15)
saved:  6
batch_id 7 64
90
6
operators_batch:  (6, 90, 15)
saved:  7
batch_id 8 64
104
6
operators_batch:  (6, 104, 15)
saved:  8
batch_id 9 64
93
7
operators_batch:  (7, 93, 15)
saved:  9
batch_id 10 64
100
7
operators_batch:  (7, 100, 15)
saved:  10
batch_id 11 64
97
6
operators_batch:  (6, 97, 15)
saved:  11
batch_id 12 64
84
6
operators_batch:  (6, 84, 15)
saved:  12
batch_id 13 64
79
6
operators_batch:  (6, 79, 15)
saved:  13
batch_id 14 64
91
7
operators_batch:  (7, 91, 15)
saved:  14
batch_id 15 64
78
7
operators_batch:  (7, 78, 15)
saved:  15
batch_id 16 64
93
7
operators_batch:

saved:  132
batch_id 133 64
92
6
operators_batch:  (6, 92, 15)
saved:  133
batch_id 134 64
92
6
operators_batch:  (6, 92, 15)
saved:  134
batch_id 135 64
89
6
operators_batch:  (6, 89, 15)
saved:  135
batch_id 136 64
96
6
operators_batch:  (6, 96, 15)
saved:  136
batch_id 137 64
93
6
operators_batch:  (6, 93, 15)
saved:  137
batch_id 138 64
104
7
operators_batch:  (7, 104, 15)
saved:  138
batch_id 139 64
97
6
operators_batch:  (6, 97, 15)
saved:  139
batch_id 140 64
103
6
operators_batch:  (6, 103, 15)
saved:  140
batch_id 141 64
77
6
operators_batch:  (6, 77, 15)
saved:  141
batch_id 142 64
95
7
operators_batch:  (7, 95, 15)
saved:  142
batch_id 143 64
95
6
operators_batch:  (6, 95, 15)
saved:  143
batch_id 144 64
90
6
operators_batch:  (6, 90, 15)
saved:  144
batch_id 145 64
89
6
operators_batch:  (6, 89, 15)
saved:  145
batch_id 146 64
99
6
operators_batch:  (6, 99, 15)
saved:  146
batch_id 147 64
95
7
operators_batch:  (7, 95, 15)
saved:  147
batch_id 148 64
83
6
operators_batch:  

83
6
operators_batch:  (6, 83, 15)
saved:  262
batch_id 263 64
96
6
operators_batch:  (6, 96, 15)
saved:  263
batch_id 264 64
95
6
operators_batch:  (6, 95, 15)
saved:  264
batch_id 265 64
97
7
operators_batch:  (7, 97, 15)
saved:  265
batch_id 266 64
97
7
operators_batch:  (7, 97, 15)
saved:  266
batch_id 267 64
93
6
operators_batch:  (6, 93, 15)
saved:  267
batch_id 268 64
81
7
operators_batch:  (7, 81, 15)
saved:  268
batch_id 269 64
92
7
operators_batch:  (7, 92, 15)
saved:  269
batch_id 270 64
93
7
operators_batch:  (7, 93, 15)
saved:  270
batch_id 271 64
98
6
operators_batch:  (6, 98, 15)
saved:  271
batch_id 272 64
91
6
operators_batch:  (6, 91, 15)
saved:  272
batch_id 273 64
77
6
operators_batch:  (6, 77, 15)
saved:  273
batch_id 274 64
92
6
operators_batch:  (6, 92, 15)
saved:  274
batch_id 275 64
88
7
operators_batch:  (7, 88, 15)
saved:  275
batch_id 276 64
86
6
operators_batch:  (6, 86, 15)
saved:  276
batch_id 277 64
101
6
operators_batch:  (6, 101, 15)
saved:  277
batch_

saved:  391
batch_id 392 64
87
6
operators_batch:  (6, 87, 15)
saved:  392
batch_id 393 64
98
6
operators_batch:  (6, 98, 15)
saved:  393
batch_id 394 64
91
6
operators_batch:  (6, 91, 15)
saved:  394
batch_id 395 64
88
6
operators_batch:  (6, 88, 15)
saved:  395
batch_id 396 64
99
6
operators_batch:  (6, 99, 15)
saved:  396
batch_id 397 64
92
7
operators_batch:  (7, 92, 15)
saved:  397
batch_id 398 64
91
6
operators_batch:  (6, 91, 15)
saved:  398
batch_id 399 64
98
6
operators_batch:  (6, 98, 15)
saved:  399
batch_id 400 64
94
7
operators_batch:  (7, 94, 15)
saved:  400
batch_id 401 64
95
6
operators_batch:  (6, 95, 15)
saved:  401
batch_id 402 64
94
5
operators_batch:  (5, 94, 15)
saved:  402
batch_id 403 64
94
7
operators_batch:  (7, 94, 15)
saved:  403
batch_id 404 64
94
7
operators_batch:  (7, 94, 15)
saved:  404
batch_id 405 64
86
6
operators_batch:  (6, 86, 15)
saved:  405
batch_id 406 64
97
7
operators_batch:  (7, 97, 15)
saved:  406
batch_id 407 64
86
7
operators_batch:  (7, 

saved:  521
batch_id 522 64
95
6
operators_batch:  (6, 95, 15)
saved:  522
batch_id 523 64
93
6
operators_batch:  (6, 93, 15)
saved:  523
batch_id 524 64
90
7
operators_batch:  (7, 90, 15)
saved:  524
batch_id 525 64
85
6
operators_batch:  (6, 85, 15)
saved:  525
batch_id 526 64
84
7
operators_batch:  (7, 84, 15)
saved:  526
batch_id 527 64
98
6
operators_batch:  (6, 98, 15)
saved:  527
batch_id 528 64
97
7
operators_batch:  (7, 97, 15)
saved:  528
batch_id 529 64
78
7
operators_batch:  (7, 78, 15)
saved:  529
batch_id 530 64
98
7
operators_batch:  (7, 98, 15)
saved:  530
batch_id 531 64
95
7
operators_batch:  (7, 95, 15)
saved:  531
batch_id 532 64
85
6
operators_batch:  (6, 85, 15)
saved:  532
batch_id 533 64
93
7
operators_batch:  (7, 93, 15)
saved:  533
batch_id 534 64
85
7
operators_batch:  (7, 85, 15)
saved:  534
batch_id 535 64
103
6
operators_batch:  (6, 103, 15)
saved:  535
batch_id 536 64
95
6
operators_batch:  (6, 95, 15)
saved:  536
batch_id 537 64
87
6
operators_batch:  (6

...

saved:  1038
batch_id 1039 64
95
7
operators_batch:  (7, 95, 15)
saved:  1039
batch_id 1040 64
92
6
operators_batch:  (6, 92, 15)
saved:  1040
batch_id 1041 64
99
7
operators_batch:  (7, 99, 15)
saved:  1041
batch_id 1042 64
91
7
operators_batch:  (7, 91, 15)
saved:  1042
batch_id 1043 64
94
6
operators_batch:  (6, 94, 15)
saved:  1043
batch_id 1044 64
87
7
operators_batch:  (7, 87, 15)
saved:  1044
batch_id 1045 64
89
6
operators_batch:  (6, 89, 15)
saved:  1045
batch_id 1046 64
90
6
operators_batch:  (6, 90, 15)
saved:  1046
batch_id 1047 64
95
6
operators_batch:  (6, 95, 15)
saved:  1047
batch_id 1048 64
87
7
operators_batch:  (7, 87, 15)
saved:  1048
batch_id 1049 64
86
6
operators_batch:  (6, 86, 15)
saved:  1049
batch_id 1050 64
96
6
operators_batch:  (6, 96, 15)
saved:  1050
batch_id 1051 64
93
7
operators_batch:  (7, 93, 15)
saved:  1051
batch_id 1052 64
105
7
operators_batch:  (7, 105, 15)
saved:  1052
batch_id 1053 64
104
6
operators_batch:  (6, 104, 15)
saved:  1053
batch_id

97
7
operators_batch:  (7, 97, 15)
saved:  1164
batch_id 1165 64
110
6
operators_batch:  (6, 110, 15)
saved:  1165
batch_id 1166 64
82
7
operators_batch:  (7, 82, 15)
saved:  1166
batch_id 1167 64
107
6
operators_batch:  (6, 107, 15)
saved:  1167
batch_id 1168 64
92
7
operators_batch:  (7, 92, 15)
saved:  1168
batch_id 1169 64
103
5
operators_batch:  (5, 103, 15)
saved:  1169
batch_id 1170 64
101
6
operators_batch:  (6, 101, 15)
saved:  1170
batch_id 1171 64
103
6
operators_batch:  (6, 103, 15)
saved:  1171
batch_id 1172 64
101
7
operators_batch:  (7, 101, 15)
saved:  1172
batch_id 1173 64
95
6
operators_batch:  (6, 95, 15)
saved:  1173
batch_id 1174 64
99
7
operators_batch:  (7, 99, 15)
saved:  1174
batch_id 1175 64
92
7
operators_batch:  (7, 92, 15)
saved:  1175
batch_id 1176 64
94
6
operators_batch:  (6, 94, 15)
saved:  1176
batch_id 1177 64
92
6
operators_batch:  (6, 92, 15)
saved:  1177
batch_id 1178 64
86
6
operators_batch:  (6, 86, 15)
saved:  1178
batch_id 1179 64
86
6
operator

99
7
operators_batch:  (7, 99, 15)
saved:  1289
batch_id 1290 64
98
6
operators_batch:  (6, 98, 15)
saved:  1290
batch_id 1291 64
92
7
operators_batch:  (7, 92, 15)
saved:  1291
batch_id 1292 64
86
6
operators_batch:  (6, 86, 15)
saved:  1292
batch_id 1293 64
90
7
operators_batch:  (7, 90, 15)
saved:  1293
batch_id 1294 64
111
7
operators_batch:  (7, 111, 15)
saved:  1294
batch_id 1295 64
92
7
operators_batch:  (7, 92, 15)
saved:  1295
batch_id 1296 64
99
6
operators_batch:  (6, 99, 15)
saved:  1296
batch_id 1297 64
80
6
operators_batch:  (6, 80, 15)
saved:  1297
batch_id 1298 64
90
6
operators_batch:  (6, 90, 15)
saved:  1298
batch_id 1299 64
102
6
operators_batch:  (6, 102, 15)
saved:  1299
batch_id 1300 64
88
7
operators_batch:  (7, 88, 15)
saved:  1300
batch_id 1301 64
86
6
operators_batch:  (6, 86, 15)
saved:  1301
batch_id 1302 64
88
7
operators_batch:  (7, 88, 15)
saved:  1302
batch_id 1303 64
95
6
operators_batch:  (6, 95, 15)
saved:  1303
batch_id 1304 64
105
6
operators_batch

saved:  1414
batch_id 1415 64
91
7
operators_batch:  (7, 91, 15)
saved:  1415
batch_id 1416 64
99
6
operators_batch:  (6, 99, 15)
saved:  1416
batch_id 1417 64
86
6
operators_batch:  (6, 86, 15)
saved:  1417
batch_id 1418 64
81
6
operators_batch:  (6, 81, 15)
saved:  1418
batch_id 1419 64
93
6
operators_batch:  (6, 93, 15)
saved:  1419
batch_id 1420 64
95
7
operators_batch:  (7, 95, 15)
saved:  1420
batch_id 1421 64
96
6
operators_batch:  (6, 96, 15)
saved:  1421
batch_id 1422 64
97
7
operators_batch:  (7, 97, 15)
saved:  1422
batch_id 1423 64
90
7
operators_batch:  (7, 90, 15)
saved:  1423
batch_id 1424 64
109
6
operators_batch:  (6, 109, 15)
saved:  1424
batch_id 1425 64
98
6
operators_batch:  (6, 98, 15)
saved:  1425
batch_id 1426 64
103
6
operators_batch:  (6, 103, 15)
saved:  1426
batch_id 1427 64
96
7
operators_batch:  (7, 96, 15)
saved:  1427
batch_id 1428 64
88
6
operators_batch:  (6, 88, 15)
saved:  1428
batch_id 1429 64
110
6
operators_batch:  (6, 110, 15)
saved:  1429
batch_

saved:  1539
batch_id 1540 64
81
6
operators_batch:  (6, 81, 15)
saved:  1540
batch_id 1541 64
96
7
operators_batch:  (7, 96, 15)
saved:  1541
batch_id 1542 64
90
6
operators_batch:  (6, 90, 15)
saved:  1542
batch_id 1543 64
85
6
operators_batch:  (6, 85, 15)
saved:  1543
batch_id 1544 64
89
7
operators_batch:  (7, 89, 15)
saved:  1544
batch_id 1545 64
97
6
operators_batch:  (6, 97, 15)
saved:  1545
batch_id 1546 64
89
7
operators_batch:  (7, 89, 15)
saved:  1546
batch_id 1547 64
93
7
operators_batch:  (7, 93, 15)
saved:  1547
batch_id 1548 64
89
6
operators_batch:  (6, 89, 15)
saved:  1548
batch_id 1549 64
97
7
operators_batch:  (7, 97, 15)
saved:  1549
batch_id 1550 64
105
7
operators_batch:  (7, 105, 15)
saved:  1550
batch_id 1551 64
94
7
operators_batch:  (7, 94, 15)
saved:  1551
batch_id 1552 64
101
7
operators_batch:  (7, 101, 15)
saved:  1552
batch_id 1553 64
81
7
operators_batch:  (7, 81, 15)
saved:  1553
batch_id 1554 64
96
7
operators_batch:  (7, 96, 15)
saved:  1554
batch_id

In [137]:
model = train(0, 1462, 1462, 1563, 20)

batch_idx:  0
batch_size:  64
Forest Evaluate Running Time:  0.013639450073242188
570.1567993164062 43.308406829833984 8141.50390625 20
batchward time:  0.3104526996612549
batch_idx:  1
batch_size:  64
Forest Evaluate Running Time:  0.01431131362915039
862.2261962890625 75.3382568359375 17433.8671875 25
batchward time:  0.06169939041137695
batch_idx:  2
batch_size:  64
Forest Evaluate Running Time:  0.013482809066772461
161.27073669433594 22.80258560180664 2713.236083984375 8
batchward time:  0.06096529960632324
batch_idx:  3
batch_size:  64
Forest Evaluate Running Time:  0.01522374153137207
219.89404296875 38.894630432128906 4715.9736328125 39
batchward time:  0.0683431625366211
batch_idx:  4
batch_size:  64
Forest Evaluate Running Time:  0.013976097106933594
378.87408447265625 13.404924392700195 19810.060546875 12
batchward time:  0.05928206443786621
batch_idx:  5
batch_size:  64
Forest Evaluate Running Time:  0.015208721160888672
79.86621856689453 11.835175514221191 1363.4765625 26


batchward time:  0.061200857162475586
batch_idx:  48
batch_size:  64
Forest Evaluate Running Time:  0.01615452766418457
53.78338623046875 14.830002784729004 1100.0562744140625 12
batchward time:  0.06745100021362305
batch_idx:  49
batch_size:  64
Forest Evaluate Running Time:  0.014245748519897461
57.60354995727539 12.221302032470703 500.5176696777344 10
batchward time:  0.06548452377319336
batch_idx:  50
batch_size:  64
Forest Evaluate Running Time:  0.014349937438964844
64.75518035888672 10.916338920593262 753.14306640625 51
batchward time:  0.09526443481445312
batch_idx:  51
batch_size:  64
Forest Evaluate Running Time:  0.015989303588867188
198.11514282226562 15.721793174743652 6311.73828125 33
batchward time:  0.05747032165527344
batch_idx:  52
batch_size:  64
Forest Evaluate Running Time:  0.014570474624633789
41.33418273925781 6.3400559425354 524.1699829101562 55
batchward time:  0.06246614456176758
batch_idx:  53
batch_size:  64
Forest Evaluate Running Time:  0.0147347450256347

batchward time:  0.06132078170776367
batch_idx:  95
batch_size:  64
Forest Evaluate Running Time:  0.012672901153564453
16.975223541259766 8.274833679199219 145.44808959960938 30
batchward time:  0.06063032150268555
batch_idx:  96
batch_size:  64
Forest Evaluate Running Time:  0.01348423957824707
14.717229843139648 5.283304691314697 94.00484466552734 16
batchward time:  0.07245540618896484
batch_idx:  97
batch_size:  64
Forest Evaluate Running Time:  0.01500391960144043
34.05766296386719 4.330590724945068 980.0941162109375 42
batchward time:  0.09768295288085938
batch_idx:  98
batch_size:  64
Forest Evaluate Running Time:  0.019084930419921875
10.861448287963867 3.8222193717956543 132.0382843017578 7
batchward time:  0.07062363624572754
batch_idx:  99
batch_size:  64
Forest Evaluate Running Time:  0.016880273818969727
11.327474594116211 5.3499884605407715 93.20568084716797 50
batchward time:  0.10124349594116211
batch_idx:  100
batch_size:  64
Forest Evaluate Running Time:  0.012790203

Forest Evaluate Running Time:  0.019741535186767578
85.88172149658203 4.722433567047119 3107.630859375 0
batchward time:  0.11097073554992676
batch_idx:  143
batch_size:  64
Forest Evaluate Running Time:  0.013960599899291992
116.504150390625 7.980762004852295 5640.2109375 40
batchward time:  0.10698914527893066
batch_idx:  144
batch_size:  64
Forest Evaluate Running Time:  0.013548612594604492
29.12596321105957 10.088167190551758 228.58250427246094 62
batchward time:  0.06758332252502441
batch_idx:  145
batch_size:  64
Forest Evaluate Running Time:  0.013323068618774414
269.3672790527344 10.888567924499512 9786.9873046875 35
batchward time:  0.08165645599365234
batch_idx:  146
batch_size:  64
Forest Evaluate Running Time:  0.014419317245483398
252.73602294921875 8.341224670410156 12470.3984375 6
batchward time:  0.07480216026306152
batch_idx:  147
batch_size:  64
Forest Evaluate Running Time:  0.016329526901245117
62.08882141113281 7.445847988128662 1369.335693359375 43
batchward time

batchward time:  0.05626344680786133
batch_idx:  190
batch_size:  64
Forest Evaluate Running Time:  0.00995182991027832
13.239907264709473 3.140348434448242 461.2201232910156 9
batchward time:  0.04729580879211426
batch_idx:  191
batch_size:  64
Forest Evaluate Running Time:  0.01002812385559082
16.304990768432617 3.880690813064575 280.64544677734375 34
batchward time:  0.04953265190124512
batch_idx:  192
batch_size:  64
Forest Evaluate Running Time:  0.013839006423950195
17.640323638916016 4.483880043029785 581.0355224609375 5
batchward time:  0.061339616775512695
batch_idx:  193
batch_size:  64
Forest Evaluate Running Time:  0.012214422225952148
49.82548904418945 4.698812961578369 2069.875732421875 40
batchward time:  0.051906585693359375
batch_idx:  194
batch_size:  64
Forest Evaluate Running Time:  0.014735937118530273
34.288333892822266 3.3107194900512695 514.0399780273438 8
batchward time:  0.09644889831542969
batch_idx:  195
batch_size:  64
Forest Evaluate Running Time:  0.02086

...

3.6477174758911133 1.1554129123687744 89.37527465820312 1
batchward time:  0.08822321891784668
batch_idx:  1314
batch_size:  64
Forest Evaluate Running Time:  0.014606475830078125
1.5860397815704346 1.229583501815796 7.613055229187012 39
batchward time:  0.09441947937011719
batch_idx:  1315
batch_size:  64
Forest Evaluate Running Time:  0.014050006866455078
2.4979355335235596 1.2112388610839844 36.246219635009766 4
batchward time:  0.07057762145996094
batch_idx:  1316
batch_size:  64
Forest Evaluate Running Time:  0.011735916137695312
6.593094348907471 1.589226245880127 121.72791290283203 13
batchward time:  0.06402230262756348
batch_idx:  1317
batch_size:  64
Forest Evaluate Running Time:  0.01319742202758789
4.069459915161133 1.2598026990890503 88.66387176513672 57
batchward time:  0.07175469398498535
batch_idx:  1318
batch_size:  64
Forest Evaluate Running Time:  0.01614999771118164
2.2252399921417236 1.2076828479766846 23.131214141845703 3
batchward time:  0.0831000804901123
batch_

batchward time:  0.06749987602233887
batch_idx:  1361
batch_size:  64
Forest Evaluate Running Time:  0.01785564422607422
5.789764881134033 1.425976037979126 151.62562561035156 1
batchward time:  0.08143758773803711
batch_idx:  1362
batch_size:  64
Forest Evaluate Running Time:  0.012643575668334961
2.766866683959961 1.3891862630844116 45.899410247802734 43
batchward time:  0.07457160949707031
batch_idx:  1363
batch_size:  64
Forest Evaluate Running Time:  0.013260364532470703
2.398019313812256 1.196936845779419 46.146339416503906 61
batchward time:  0.07122421264648438
batch_idx:  1364
batch_size:  64
Forest Evaluate Running Time:  0.016051292419433594
2.228501319885254 1.2866572141647339 12.494894027709961 41
batchward time:  0.07603025436401367
batch_idx:  1365
batch_size:  64
Forest Evaluate Running Time:  0.01742386817932129
2.2900123596191406 1.2245761156082153 53.813758850097656 17
batchward time:  0.08015799522399902
batch_idx:  1366
batch_size:  64
Forest Evaluate Running Time:

batchward time:  0.05959439277648926
batch_idx:  1408
batch_size:  64
Forest Evaluate Running Time:  0.012138843536376953
2.692366361618042 1.297155499458313 30.44366455078125 18
batchward time:  0.06171703338623047
batch_idx:  1409
batch_size:  64
Forest Evaluate Running Time:  0.01121377944946289
2.3400678634643555 1.1936709880828857 16.120996475219727 26
batchward time:  0.059653282165527344
batch_idx:  1410
batch_size:  64
Forest Evaluate Running Time:  0.013016462326049805
2.3784334659576416 1.336319088935852 18.21084976196289 32
batchward time:  0.13066387176513672
batch_idx:  1411
batch_size:  64
Forest Evaluate Running Time:  0.014580726623535156
2.6864404678344727 1.3226739168167114 21.923189163208008 53
batchward time:  0.0692899227142334
batch_idx:  1412
batch_size:  64
Forest Evaluate Running Time:  0.01862311363220215
2.907665491104126 1.3848211765289307 31.475109100341797 55
batchward time:  0.08439159393310547
batch_idx:  1413
batch_size:  64
Forest Evaluate Running Time

batchward time:  0.07860207557678223
batch_idx:  1455
batch_size:  64
Forest Evaluate Running Time:  0.01347494125366211
2.2006077766418457 1.2619985342025757 20.285537719726562 35
batchward time:  0.08821535110473633
batch_idx:  1456
batch_size:  64
Forest Evaluate Running Time:  0.021183252334594727
3.024354934692383 1.3799183368682861 24.59634017944336 32
batchward time:  0.08174300193786621
batch_idx:  1457
batch_size:  64
Forest Evaluate Running Time:  0.017684459686279297
1.7248430252075195 1.3547158241271973 11.257835388183594 23
batchward time:  0.09450006484985352
batch_idx:  1458
batch_size:  64
Forest Evaluate Running Time:  0.01418757438659668
2.9031617641448975 1.2586029767990112 47.42732620239258 5
batchward time:  0.10506319999694824
batch_idx:  1459
batch_size:  64
Forest Evaluate Running Time:  0.01801586151123047
3.1415140628814697 1.4077509641647339 31.062854766845703 12
batchward time:  0.09990310668945312
batch_idx:  1460
batch_size:  64
Forest Evaluate Running Tim

batch_size:  64
Forest Evaluate Running Time:  0.009232521057128906
2.1519200801849365 1.3186713457107544 18.023305892944336 48
batch_idx:  1515
batch_size:  64
Forest Evaluate Running Time:  0.009415626525878906
2.464834690093994 1.3431615829467773 40.953914642333984 14
batch_idx:  1516
batch_size:  64
Forest Evaluate Running Time:  0.010396480560302734
3.1419105529785156 1.2552024126052856 41.725433349609375 25
batch_idx:  1517
batch_size:  64
Forest Evaluate Running Time:  0.011361122131347656
5.257351398468018 1.5826984643936157 64.43635559082031 15
batch_idx:  1518
batch_size:  64
Forest Evaluate Running Time:  0.013202190399169922
2.7317802906036377 1.556647539138794 28.627103805541992 27
batch_idx:  1519
batch_size:  64
Forest Evaluate Running Time:  0.017041921615600586
2.5800764560699463 1.3162715435028076 24.189359664916992 19
batch_idx:  1520
batch_size:  64
Forest Evaluate Running Time:  0.015251398086547852
3.534247636795044 1.5295469760894775 67.28750610351562 17
batch_id

In [119]:
x = np.array([1 for _ in range(4)])
y = np.array([0 for _ in range(4)])
np.minimum(x, y)

array([0, 0, 0, 0])